In [114]:
## Imports
import sys
sys.path.append('../src/dataStructures')
sys.path.append('../src/utilities')
import itertools
import time
import numpy as np
import dask.array as da
import matplotlib.pyplot as plt
import bisect
from scipy.special import sph_harm
from pyevtk.hl import pointsToVTK

from meshUtilities import *
ThreeByThreeByThree = [element for element in itertools.product(range(3),range(3),range(3))]

from TreeStruct_CC import Tree


In [115]:
## Create tree, return np.arrays x, y, z, and w
def testDask(domain,order,minDepth, maxDepth, additionalDepthAtAtoms, divideCriterion, 
                          divideParameter1, divideParameter2=0.0, divideParameter3=0.0, divideParameter4=0.0, 
                          smoothingEpsilon=0.0, 
                          inputFile='', outputFile='',
                          savedMesh=''):    
    
    
#     [coordinateFile, DummyOutputFile] = np.genfromtxt(inputFile,dtype="|U100")[:2]
    [coordinateFile, referenceEigenvaluesFile, DummyOutputFile] = np.genfromtxt(inputFile,dtype="|U100")[:3]
    [Eband, Ekinetic, Eexchange, Ecorrelation, Eelectrostatic, Etotal] = np.genfromtxt(inputFile)[3:]
#     nElectrons = int(nElectrons)
#     nOrbitals = int(nOrbitals)

    print('Reading atomic coordinates from: ', coordinateFile)
    atomData = np.genfromtxt(coordinateFile,delimiter=',',dtype=float)
    if np.shape(atomData)==(5,):
        nElectrons = atomData[3]
    else:
        nElectrons = 0
        for i in range(len(atomData)):
            nElectrons += atomData[i,3]
    
#     nOrbitals = int( np.ceil(nElectrons/2))
    nOrbitals = int( np.ceil(nElectrons/2)+1)

    if inputFile=='../src/utilities/molecularConfigurations/benzeneAuxiliary.csv':
        nOrbitals = 30
        
    if inputFile=='../src/utilities/molecularConfigurations/O2Auxiliary.csv':
        nOrbitals = 10
        
    print('nElectrons = ', nElectrons)
    print('nOrbitals  = ', nOrbitals)
    print([coordinateFile, Etotal, Eexchange, Ecorrelation, Eband])
    tree = Tree(-domain,domain,order,-domain,domain,order,-domain,domain,order,nElectrons,nOrbitals,additionalDepthAtAtoms=additionalDepthAtAtoms,minDepth=minDepth,gaugeShift=gaugeShift,
                coordinateFile=coordinateFile,smoothingEps=smoothingEpsilon,inputFile=inputFile)#, iterationOutFile=outputFile)

    
    print('max depth ', maxDepth)
    tree.minimalBuildTree( maxLevels=maxDepth, initializationType='atomic',divideCriterion=divideCriterion, 
                    divideParameter1=divideParameter1, divideParameter2=divideParameter2, divideParameter3=divideParameter3, divideParameter4=divideParameter4, 
                    savedMesh=savedMesh, printTreeProperties=True,onlyFillOne=False)
    
    x,y,z,w = tree.extractXYZ()
    return x,y,z,w, nOrbitals, tree.atoms
tree=None

gaugeShift=-0.5 
    
x,y,z,w,nWavefunctions,atoms = testDask(domain=20,order=5,
    minDepth=3, maxDepth=20, additionalDepthAtAtoms=0, divideCriterion='LW5', 
    divideParameter1=500, divideParameter2=1e6, divideParameter3=3e-5, divideParameter4=0,
    smoothingEpsilon=0.0,inputFile='../src/utilities/molecularConfigurations/oxygenAtomAuxiliary.csv', 
    outputFile='/Users/nathanvaughn/Desktop/meshTests/O2/aspectRatioTesting',
    savedMesh='')
tree=None


Reading atomic coordinates from:  ../src/utilities/molecularConfigurations/oxygenAtom.csv
nElectrons =  8.0
nOrbitals  =  5
['../src/utilities/molecularConfigurations/oxygenAtom.csv', -74.46933750109882, -7.219370082893998, -0.5445532356878884, -40.613397710076626]
Reading atomic coordinates from:  ../src/utilities/molecularConfigurations/oxygenAtom.csv
Using single atom data from:
/Users/nathanvaughn/AtomicData/allElectron/z8/singleAtomData/
Gauge shift  -0.5

~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
~~~~~~~~~~~~~~~~~~~~~~~ Atoms ~~~~~~~~~~~~~~~~~~~~~~~
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
Z = 8 located at (x, y, z) = ( 0.000,  0.000,  0.000)
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~

max depth  20
Number of cells at max depth:  0
Saving mesh to tree.saveList
/Users/nathanvaughn/Documents/GitHub/Greens-Functions-Iterative-Methods/3D-Gree

../src/dataStructures/TreeStruct_CC.py:303: RuntimeWarning: divide by zero encountered in double_scalars
  xRatio = np.max([Cell.xmax-Atom.x, Atom.x-Cell.xmin] ) / np.min([Cell.xmax-Atom.x, Atom.x-Cell.xmin] )
../src/dataStructures/TreeStruct_CC.py:304: RuntimeWarning: divide by zero encountered in double_scalars
  yRatio = np.max([Cell.ymax-Atom.y, Atom.y-Cell.ymin] ) / np.min([Cell.ymax-Atom.y,Atom.y-Cell.ymin] )
../src/dataStructures/TreeStruct_CC.py:305: RuntimeWarning: divide by zero encountered in double_scalars
  zRatio = np.max([Cell.zmax-Atom.z, Atom.z-Cell.zmin] ) / np.min([Cell.zmax-Atom.z, Atom.z-Cell.zmin] )


Added level 11 to dictionary.
Number of cells at each level: 
{3: 480, 4: 200, 5: 392, 6: 416, 7: 224, 8: 248, 9: 56, 10: 56, 11: 64}
Number of gridpoints:  267000
Tree build completed. 
Domain Size:                                 [-20.0, 20.0] 
Divide Criterion:                            LW5 
Divide Parameter1:                           5.00e+02 
Divide Parameter2:                           1.00e+06 
Divide Parameter3:                           3.00e-05 
Divide Parameter4:                           0.00e+00 
Total Number of Cells:                       2441 
Total Number of Leaf Cells:                  2136 
Total Number of Gridpoints:                  267000 
Minimum Depth                                3 levels 
Maximum Depth from refinement scheme:        11 levels 
Additional refinement to depth:              11 levels 
Cell Order:                                  5 
Construction time:                           4.07 seconds.


In [116]:
## Convert to dask arrays
CHUNKSIZE="auto"
CHUNKSIZE=10000
X = da.from_array(x,chunks=(CHUNKSIZE,))
Y = da.from_array(y,chunks=(CHUNKSIZE,))
Z = da.from_array(z,chunks=(CHUNKSIZE,))
W = da.from_array(w,chunks=(CHUNKSIZE,))
nPoints = len(x)


print('x: ', np.shape(x))
print('y: ', np.shape(y))
print('z: ', np.shape(z))
print('w: ', np.shape(w))

print('X: ', X)
print('Y: ', Y)
print('Z: ', Z)
print('W: ', W)


x:  (267000,)
y:  (267000,)
z:  (267000,)
w:  (267000,)
X:  dask.array<array, shape=(267000,), dtype=float64, chunksize=(10000,)>
Y:  dask.array<array, shape=(267000,), dtype=float64, chunksize=(10000,)>
Z:  dask.array<array, shape=(267000,), dtype=float64, chunksize=(10000,)>
W:  dask.array<array, shape=(267000,), dtype=float64, chunksize=(10000,)>


In [117]:
## Initialize Density and Potential Arrays
Vext = da.zeros( (nPoints,), chunks=(CHUNKSIZE,))
rho = da.zeros( (nPoints,), chunks=(CHUNKSIZE,))
# rho = np.zeros( (nPoints,))

totalElectrons=0

for atom in atoms:
    totalElectrons += atom.atomicNumber
    r = np.sqrt( (X-atom.x)**2 + (Y-atom.y)**2 + (Z-atom.z)**2 )
    print('created r')
    try:
        print('Incrementing rho')
        rho += atom.interpolators['density'](r)
        Vext += atom.V(X,Y,Z)
    except ValueError:
        rho += 0.0   # if outside the interpolation range, assume 0.
    print("max density: ", max(abs(rho.compute())))
    print("max density: ", rho.max().compute())

print(rho)
print(Vext)
# Vext.compute()


created r
Incrementing rho
max density:  304.558074779286
max density:  304.558074779286
dask.array<add, shape=(267000,), dtype=float64, chunksize=(10000,)>
dask.array<add, shape=(267000,), dtype=float64, chunksize=(10000,)>


In [118]:
## Initialize Wavefunction Arrays
from dask.diagnostics import Profiler, ResourceProfiler, CacheProfiler, visualize
wavefunctions = {}
for i in range(nWavefunctions):
    wavefunctions[i] = da.zeros( (nPoints,), chunks=(CHUNKSIZE,) )

def initializeOrbitalsFromAtomicDataExternally(): 
        aufbauList = ['10',                                     # n+ell = 1
                      '20',                                     # n+ell = 2
                      '21', '30',                               # n+ell = 3
                      '31', '40', 
                      '32', '41', '50'
                      '42', '51', '60'
                      '43', '52', '61', '70']

        orbitalIndex=0
    
        for atom in atoms:
            nAtomicOrbitals = atom.nAtomicOrbitals
                
            print('Initializing orbitals for atom Z = %i located at (x, y, z) = (%6.3f, %6.3f, %6.3f)' 
                      %(atom.atomicNumber, atom.x,atom.y,atom.z))
            print('Orbital index = %i'%orbitalIndex)            
            singleAtomOrbitalCount=0
            for nell in aufbauList:
                
                if singleAtomOrbitalCount< nAtomicOrbitals:  
                    n = int(nell[0])
                    ell = int(nell[1])
                    psiID = 'psi'+str(n)+str(ell)
                    print('psiID: ', psiID)
                    for m in range(-ell,ell+1):
                        
                        dx = X-atom.x
                        dy = Y-atom.y
                        dz = Z-atom.z
            
                        r = np.sqrt( dx**2 + dy**2 + dz**2 )
                        inclination = np.arccos(dz/r)
                        azimuthal = np.arctan2(dy,dx)
                        
                        if m<0:
                            Ysph = (sph_harm(m,ell,azimuthal,inclination) + (-1)**m * sph_harm(-m,ell,azimuthal,inclination))/np.sqrt(2) 
                        if m>0:
                            Ysph = 1j*(sph_harm(m,ell,azimuthal,inclination) - (-1)**m * sph_harm(-m,ell,azimuthal,inclination))/np.sqrt(2)
                        if ( m==0 ):
                            Ysph = sph_harm(m,ell,azimuthal,inclination)
                        if np.max( abs(np.imag(Ysph)) ) > 1e-14:
                            print('imag(Ysph) ', np.imag(Ysph))
                            return
                        try:
                            wavefunctions[orbitalIndex] = atom.interpolators[psiID](r)*np.real(Ysph)
                        except ValueError:
                            wavefunctions[orbitalIndex] = 0.0   # if outside the interpolation range, assume 0.
                        
                                                
                        print('Orbital %i filled with (n,ell,m) = (%i,%i,%i) ' %(orbitalIndex,n,ell,m))
                        orbitalIndex += 1
                        singleAtomOrbitalCount += 1

                        
# print(wavefunctions.compute() )  

# print(wavefunctions)
print( sys.getsizeof(wavefunctions) )
print( sys.getsizeof(wavefunctions[0]) )
print( sys.getsizeof(wavefunctions[0].compute()) )

with Profiler() as prof, ResourceProfiler(dt=0.25) as rprof, CacheProfiler() as cprof:
    initializeOrbitalsFromAtomicDataExternally()
# print(wavefunctions[0].compute())
# print(wavefunctions[1].compute())
# print(wavefunctions[2].compute())
print( sys.getsizeof(wavefunctions) )
print( sys.getsizeof(wavefunctions[0].compute()) )
print( sys.getsizeof(wavefunctions[4].compute()) )
prof.results[0]
# visualize([prof, rprof, cprof])

240
80
2136096
Initializing orbitals for atom Z = 8 located at (x, y, z) = ( 0.000,  0.000,  0.000)
Orbital index = 0
psiID:  psi10
Orbital 0 filled with (n,ell,m) = (1,0,0) 
psiID:  psi20
Orbital 1 filled with (n,ell,m) = (2,0,0) 
psiID:  psi21
Orbital 2 filled with (n,ell,m) = (2,1,-1) 
Orbital 3 filled with (n,ell,m) = (2,1,0) 
Orbital 4 filled with (n,ell,m) = (2,1,1) 
240
2136096
2136096


bokeh.models.layouts.Column(
    id='45ece5d6-08ba-4098-9fe5-719a29708903',
    children=[bokeh.models.tools.ToolbarBox(
         id='f889d1d8-920e-4ecb-af8c-9d964471616d',
         css_classes=[],
         disabled=False,
         height=None,
         js_event_callbacks={},
         js_property_callbacks={},
         name=None,
         sizing_mode='fixed',
         subscribed_events=[],
         tags=[],
         toolbar=bokeh.models.tools.ProxyToolbar(
             id='f243e60c-2c82-4db6-af30-05d2f61cdf3b',
             js_event_callbacks={},
             js_property_callbacks={},
             logo='normal',
             name=None,
             subscribed_events=[],
             tags=[],
             tools=[bokeh.models.tools.HoverTool(
                  id='cfe6c152-e8fb-4136-b8e9-7ab533755324',
                  anchor='center',
                  attachment='horizontal',
                  callback=None,
                  formatters={},
                  js_event_callbacks={},
                  js_property_callbacks={},
                  line_policy='nearest',
                  mode='mouse',
                  name=None,
                  names=[],
                  point_policy='follow_mouse',
                  renderers='auto',
                  show_arrow=True,
                  subscribed_events=[],
                  tags=[],
                  toggleable=True,
                  tooltips='\n    <div>\n        <span style="font-size: 14px; font-weight: bold;">Key:</span>&nbsp;\n        <span style="font-size: 10px; font-family: Monaco, monospace;">@key</span>\n    </div>\n    <div>\n        <span style="font-size: 14px; font-weight: bold;">Task:</span>&nbsp;\n        <span style="font-size: 10px; font-family: Monaco, monospace;">@function</span>\n    </div>\n    '),
              bokeh.models.tools.SaveTool(
                  id='328ba689-85e2-42b3-8a34-5e3b2875ed5c',
                  js_event_callbacks={},
                  js_property_callbacks={},
                  name=None,
                  subscribed_events=[],
                  tags=[]),
              bokeh.models.tools.ResetTool(
                  id='3e93f278-3561-4cc9-9f0c-7b1488a93ac6',
                  js_event_callbacks={},
                  js_property_callbacks={},
                  name=None,
                  subscribed_events=[],
                  tags=[]),
              bokeh.models.tools.WheelZoomTool(
                  id='489d7288-e90e-4406-99e0-0fb3c199d7d4',
                  dimensions='width',
                  js_event_callbacks={},
                  js_property_callbacks={},
                  maintain_focus=True,
                  name=None,
                  speed=0.0016666666666666668,
                  subscribed_events=[],
                  tags=[],
                  zoom_on_axis=True),
              bokeh.models.tools.PanTool(
                  id='fae157cd-aa7e-48fe-a7d6-53ed4d19675e',
                  dimensions='width',
                  js_event_callbacks={},
                  js_property_callbacks={},
                  name=None,
                  subscribed_events=[],
                  tags=[]),
              bokeh.models.tools.SaveTool(
                  id='5d86420e-51a9-4092-a420-213c7c30c929',
                  js_event_callbacks={},
                  js_property_callbacks={},
                  name=None,
                  subscribed_events=[],
                  tags=[]),
              bokeh.models.tools.ResetTool(
                  id='00ee7085-b541-426e-884b-732619651f9b',
                  js_event_callbacks={},
                  js_property_callbacks={},
                  name=None,
                  subscribed_events=[],
                  tags=[]),
              bokeh.models.tools.WheelZoomTool(
                  id='2bbe537a-a84f-4858-b42d-4a4da282367c',
                  dimensions='width',
                  js_event_callbacks={},
                  js_property_callbacks={},
                  maintain_focus=True,
     

In [129]:
## Compute Vxc and Veff
import pylibxc
polarization="unpolarized"
exchangeFunctional="LDA_X"
correlationFunctional="LDA_C_PZ"

exchangeFunctional = pylibxc.LibXCFunctional(exchangeFunctional, polarization)
correlationFunctional = pylibxc.LibXCFunctional(correlationFunctional, polarization)




exchangeOutput = exchangeFunctional.compute(rho.compute())
correlationOutput = correlationFunctional.compute(rho.compute())
print(exchangeOutput)
# print(type(exchangeOutput['zk']))
# print(np.shape(exchangeOutput['zk']))
epsilon_exchange = da.from_array( np.reshape(exchangeOutput['zk'],(nPoints,)), chunks=CHUNKSIZE )
epsilon_correlation = da.from_array( np.reshape(correlationOutput['zk'],(nPoints,)), chunks=CHUNKSIZE)

VRHO_exchange = da.from_array( np.reshape(exchangeOutput['vrho'],(nPoints,)), chunks=CHUNKSIZE) 
VRHO_correlation = da.from_array( np.reshape(correlationOutput['vrho'],(nPoints,)), chunks=CHUNKSIZE)

print(VRHO_exchange)
Vgauge=-0.5
# pretend Vhartree had been computed already...
Vhartree = da.from_array(np.ones((nPoints,)),chunks=CHUNKSIZE)
Veff = Vhartree + VRHO_exchange + VRHO_correlation + Vext + Vgauge

print(Veff)

{'zk': array([[0., 0., 0., ..., 0., 0., 0.]]), 'vrho': array([[0., 0., 0., ..., 0., 0., 0.]])}
dask.array<array, shape=(267000,), dtype=float64, chunksize=(10000,)>
dask.array<add, shape=(267000,), dtype=float64, chunksize=(10000,)>


In [140]:
## Compute Vxc and Veff with Dask.delayed()
import pylibxc
import dask
polarization="unpolarized"
exchangeFunctional="LDA_X"
correlationFunctional="LDA_C_PZ"

exchangeFunctional = pylibxc.LibXCFunctional(exchangeFunctional, polarization)
correlationFunctional = pylibxc.LibXCFunctional(correlationFunctional, polarization)




temp = dask.delayed( exchangeFunctional.compute )  # delayed function
print('Defined temp')

exchangeOutputZ = temp(rho)['zk']  # setting up delayed function, but not calling it yet.
exchangeOutputV = temp(rho)['vrho']  # setting up delayed function, but not calling it yet.
exZ = da.from_delayed(exchangeOutputZ, (nPoints,), dict)
exV = da.from_delayed(exchangeOutputV, (nPoints,), dict)
print(ex)
print(ex.compute())

###  This allows me to call the pylibxc function on rho, which itself is not an array but a dask.array.
###  However, the output has chunksize=nPoints.  Documentation says this array will always be created in 1 chunk.
###  The output is actually a dictionary of 'vrho' and 'zk'. 
###  Is this okay?  The density might be spread out to many processors.

# exchangeOutput.compute()
# correlationOutput = dask.delayed(correlationFunctional.compute(rho))

# epsilon_exchange = da.from_array( np.reshape(exchangeOutput['zk'],(nPoints,)), chunks=CHUNKSIZE )
# epsilon_correlation = da.from_array( np.reshape(correlationOutput['zk'],(nPoints,)), chunks=CHUNKSIZE)

# VRHO_exchange = da.from_array( np.reshape(exchangeOutput['vrho'],(nPoints,)), chunks=CHUNKSIZE) 
# VRHO_correlation = da.from_array( np.reshape(correlationOutput['vrho'],(nPoints,)), chunks=CHUNKSIZE)

# print(VRHO_exchange)
# Vgauge=-0.5
# # pretend Vhartree had been computed already...
# Vhartree = da.from_array(np.ones((nPoints,)),chunks=CHUNKSIZE)
# Veff = Vhartree + VRHO_exchange + VRHO_correlation + Vext + Vgauge

# print(Veff)

Defined temp
dask.array<from-value, shape=(1,), dtype=object, chunksize=(1,)>
[[0. 0. 0. ... 0. 0. 0.]]
